In [1]:
import os
import gc
import random as rn

from itertools import product

import pandas as pd
import numpy as np

from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold

import tensorflow as tf
from keras import backend as K
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.python.client import device_lib

import matplotlib as mpl
import matplotlib.pyplot as plt

In [2]:
os.environ["CUDA_VISIBLE_DEVICES"] = "0"

In [3]:
np.random.seed(35)
rn.seed(35)
tf.random.set_seed(35)
#print(device_lib.list_local_devices()) 

In [4]:
file_path = "../../data/BG Ex data/"
data = np.load("../../data/BG_Fold_Info.npz", allow_pickle=True)

train_files = data["train"]
test_files = data["test"]

In [5]:
param12 = {
    "FOLD_NUM": [i for i in range(10)],
    "SEQ_LEN": [12],
    "BATCH_SIZE": [128, 256],
    "HIDDEN": [12, 24, 36]
}

param24 = {
    "FOLD_NUM": [i for i in range(10)],
    "SEQ_LEN": [24],
    "BATCH_SIZE": [128, 256],
    "HIDDEN": [24, 48, 72]
}

param36 = {
    "FOLD_NUM": [i for i in range(10)],
    "SEQ_LEN": [36],
    "BATCH_SIZE": [128, 256],
    "HIDDEN": [36, 72, 108]
}

In [6]:
def expand_grid(dict_):
    return pd.DataFrame([row for row in product(*dict_.values())], columns=dict_.keys())

In [7]:
params = pd.concat([expand_grid(param12), expand_grid(param24), expand_grid(param36)])
params.reset_index(inplace=True)
params.drop("index", axis=1, inplace=True)
params

FOLD_NUM  SEQ_LEN  BATCH_SIZE  HIDDEN
0           0       12         128      12
1           0       12         128      24
2           0       12         128      36
3           0       12         256      12
4           0       12         256      24
..        ...      ...         ...     ...
175         9       36         128      72
176         9       36         128     108
177         9       36         256      36
178         9       36         256      72
179         9       36         256     108

[180 rows x 4 columns]

In [8]:
def root_mean_squared_error(y_true, y_pred):
        return K.sqrt(K.mean(K.square(y_pred - y_true))) 

In [9]:
class Model_learning:
    
    def __init__(self, FOLD, SEQ, BATCH, HIDDEN):
        
        self.train_x = None
        self.train_y = None
        
        self.test_x = None
        self.test_y = None
        
        self.train_univ = None
        self.train_univ = None
        
        self.test_univ = None
        self.test_univ = None
        
        self.FOLD=FOLD
        self.SEQ=SEQ
        self.BATCH=BATCH
        self.HIDDEN=HIDDEN
        
    def __del__(self):
        
        print("Remove Success\n")
        
    def Print_params(self):
        
        print("FOLD:", self.FOLD)
        print("SEQ:", self.SEQ)
        print("BATCH:", self.BATCH)
        print("HIDDEN:", self.HIDDEN)
        
    def Add_data(self):
        
        train_data = []
        train_x, train_y = [], []
        
        for file in train_files[self.FOLD]:
            train_data.append(np.load(file_path+file+".npz"))
            
        for i in range(len(train_data)):
            train_x.append(train_data[i]["gen"+str(self.SEQ)])
            train_y.append(train_data[i]["y"+str(self.SEQ)].astype(np.float32))
            
        test_data = []
        test_x, test_y = [], []
        
        for file in test_files[self.FOLD]:
            test_data.append(np.load(file_path+file+".npz"))
            
        for i in range(len(test_data)):
            test_x.append(test_data[i]["gen"+str(self.SEQ)])
            test_y.append(test_data[i]["y"+str(self.SEQ)].astype(np.float32))
            
        self.train_x = np.concatenate(train_x).reshape(-1, self.SEQ, 1)
        self.train_y = np.concatenate(train_y).reshape(-1, 1)
        
        self.test_x = np.concatenate(test_x).reshape(-1, self.SEQ, 1)
        self.test_y = np.concatenate(test_y).reshape(-1, 1)
            
    def Print_data(self):
        
        print("Train:", self.train_x.shape, self.train_y.shape)
        print("Test:", self.test_x.shape, self.test_y.shape)
        
    def Stack_data(self):

        train_univ = tf.data.Dataset.from_tensor_slices((self.train_x, self.train_y))
        self.train_univ = train_univ.cache().shuffle(len(self.train_x)).batch(self.BATCH).repeat()

        test_univ = tf.data.Dataset.from_tensor_slices((self.test_x, self.test_y))
        self.test_univ = test_univ.batch(self.BATCH).repeat()
        
    def RNN_learning(self):
        
        tf.keras.backend.clear_session()
        
        save_model_path = "../../model/Fold"+str(self.FOLD)+"/RNN_"+str(self.SEQ)+"_"+str(self.HIDDEN)+"_"+str(self.BATCH)+".h5"
        
        if not os.path.exists(save_model_path):
            with tf.device('/GPU:0'):
                rnn_model = tf.keras.models.Sequential([
                    tf.keras.layers.SimpleRNN(self.HIDDEN, input_shape=self.train_x.shape[-2:]),
                    tf.keras.layers.Dense(1)
                ])

                rnn_model.compile(optimizer="adam", loss=root_mean_squared_error)
        
        
                rnn_model.fit(self.train_univ,
                              epochs=100,
                              steps_per_epoch=int(len(self.train_x)/self.BATCH),
                              validation_data=self.test_univ,
                              validation_steps=int(len(self.test_x)/self.BATCH))
        
            print("RNN learn complete")
        
            rnn_model.save(save_model_path)

    def LSTM_learning(self):
        
        tf.keras.backend.clear_session()
        
        save_model_path = "../../model/Fold"+str(self.FOLD)+"/LSTM_"+str(self.SEQ)+"_"+str(self.HIDDEN)+"_"+str(self.BATCH)+".h5"
        
        if not os.path.exists(save_model_path):
            with tf.device("/GPU:0"):
                lstm_model = tf.keras.models.Sequential([
                    tf.keras.layers.LSTM(self.HIDDEN, input_shape=self.train_x.shape[-2:]),
                    tf.keras.layers.Dense(1)
                ])

                lstm_model.compile(optimizer="adam", loss=root_mean_squared_error)

                lstm_model.fit(self.train_univ,
                               epochs=100,
                               steps_per_epoch=int(len(self.train_x)/self.BATCH),
                               validation_data=self.test_univ,
                               validation_steps=int(len(self.test_x)/self.BATCH))
        
            print("LSTM learn complete")
        
            lstm_model.save(save_model_path)     
    
    def STACKLSTM_learning(self):
        
        tf.keras.backend.clear_session()
        
        save_model_path = "../../model/Fold"+str(self.FOLD)+"/STACKLSTM_"+str(self.SEQ)+"_"+str(self.HIDDEN)+"_"+str(self.BATCH)+".h5"

        if not os.path.exists(save_model_path):
            with tf.device("/GPU:0"):
                stack_lstm_model = tf.keras.models.Sequential([
                    tf.keras.layers.LSTM(self.HIDDEN, input_shape=self.train_x.shape[-2:], return_sequences=True),
                    tf.keras.layers.LSTM(self.HIDDEN, return_sequences=False),
                    tf.keras.layers.Dense(1)
                ])

                stack_lstm_model.compile(optimizer="adam", loss=root_mean_squared_error)

                stack_lstm_model.fit(self.train_univ,
                                     epochs=100,
                                     steps_per_epoch=int(len(self.train_x)/self.BATCH),
                                     validation_data=self.test_univ,
                                     validation_steps=int(len(self.test_x)/self.BATCH))
        
            print("STACKLSTM learn complete")
        
            stack_lstm_model.save(save_model_path)     

    def BILSTM_learning(self):
        
        tf.keras.backend.clear_session()
        
        save_model_path = "../../model/Fold"+str(self.FOLD)+"/BILSTM_"+str(self.SEQ)+"_"+str(self.HIDDEN)+"_"+str(self.BATCH)+".h5"

        if not os.path.exists(save_model_path):
            with tf.device("/GPU:0"):
                bilstm_model = tf.keras.models.Sequential([
                    tf.keras.layers.Bidirectional(
                        tf.keras.layers.LSTM(self.HIDDEN),
                        input_shape=self.train_x.shape[-2:]
                    ),
                    tf.keras.layers.Dense(1)
                ])

                bilstm_model.compile(optimizer="adam", loss=root_mean_squared_error)

                bilstm_model.fit(self.train_univ,
                                 epochs=100,
                                 steps_per_epoch=int(len(self.train_x)/self.BATCH),
                                 validation_data=self.test_univ,
                                 validation_steps=int(len(self.test_x)/self.BATCH))
        
            print("BILSTM learn complete")
        
            bilstm_model.save(save_model_path)     

    def GRU_learning(self):
        
        tf.keras.backend.clear_session()
        
        save_model_path = "../../model/Fold"+str(self.FOLD)+"/GRU_"+str(self.SEQ)+"_"+str(self.HIDDEN)+"_"+str(self.BATCH)+".h5"
        
        if not os.path.exists(save_model_path):
            with tf.device("/GPU:0"):
                gru_model = tf.keras.models.Sequential([
                    tf.keras.layers.GRU(self.HIDDEN, input_shape=self.train_x.shape[-2:]),
                    tf.keras.layers.Dense(1)
                ])

                gru_model.compile(optimizer="adam", loss=root_mean_squared_error)

                gru_model.fit(self.train_univ,
                              epochs=100,
                              steps_per_epoch=int(len(self.train_x)/self.BATCH),
                              validation_data=self.test_univ,
                              validation_steps=int(len(self.test_x)/self.BATCH))
        
            print("GRU learn complete")
        
            gru_model.save(save_model_path)


In [10]:
directory = "../../model/"

if not os.path.exists(directory):
    os.makedirs(directory)
    
directory = "../../model/Fold"
for i in range(10):
    if not os.path.exists(directory+str(i)+"/"):
        os.makedirs(directory+str(i)+"/")

for i in range(len(params)):
    
    ML = Model_learning(
        FOLD = params.FOLD_NUM[i],
        SEQ = params.SEQ_LEN[i],
        BATCH = params.BATCH_SIZE[i],
        HIDDEN = params.HIDDEN[i]
    )
    
    ML.Print_params()
    
    ML.Add_data()
    ML.Print_data()
    ML.Stack_data()

    ML.RNN_learning()
    ML.LSTM_learning()
    ML.STACKLSTM_learning()
    ML.BILSTM_learning()
    ML.GRU_learning()
    
    del(ML)
    gc.collect()

FOLD: 0
SEQ: 12
BATCH: 128
HIDDEN: 12
Train: (136038, 12, 1) (136038, 1)
Test: (15189, 12, 1) (15189, 1)
Remove Success

FOLD: 0
SEQ: 12
BATCH: 128
HIDDEN: 24
Train: (136038, 12, 1) (136038, 1)
Test: (15189, 12, 1) (15189, 1)
Remove Success

FOLD: 0
SEQ: 12
BATCH: 128
HIDDEN: 36
Train: (136038, 12, 1) (136038, 1)
Test: (15189, 12, 1) (15189, 1)
Remove Success

FOLD: 0
SEQ: 12
BATCH: 256
HIDDEN: 12
Train: (136038, 12, 1) (136038, 1)
Test: (15189, 12, 1) (15189, 1)
Remove Success

FOLD: 0
SEQ: 12
BATCH: 256
HIDDEN: 24
Train: (136038, 12, 1) (136038, 1)
Test: (15189, 12, 1) (15189, 1)
Remove Success

FOLD: 0
SEQ: 12
BATCH: 256
HIDDEN: 36
Train: (136038, 12, 1) (136038, 1)
Test: (15189, 12, 1) (15189, 1)
Remove Success

FOLD: 1
SEQ: 12
BATCH: 128
HIDDEN: 12
Train: (138369, 12, 1) (138369, 1)
Test: (12858, 12, 1) (12858, 1)
Remove Success

FOLD: 1
SEQ: 12
BATCH: 128
HIDDEN: 24
Train: (138369, 12, 1) (138369, 1)
Test: (12858, 12, 1) (12858, 1)
Remove Success

FOLD: 1
SEQ: 12
BATCH: 128
HIDDE

Train: (138369, 24, 1) (138369, 1)
Test: (12858, 24, 1) (12858, 1)
Epoch 1/100
1081/1081 [==============================] - 17s 13ms/step - loss: 131.0397 - val_loss: 57.9021
Epoch 2/100
1081/1081 [==============================] - 14s 13ms/step - loss: 54.9990 - val_loss: 27.3650
Epoch 3/100
1081/1081 [==============================] - 18s 16ms/step - loss: 32.5811 - val_loss: 22.4481
Epoch 4/100
1081/1081 [==============================] - 16s 15ms/step - loss: 25.6224 - val_loss: 20.4832
Epoch 5/100
1081/1081 [==============================] - 16s 14ms/step - loss: 23.5284 - val_loss: 19.9983
Epoch 6/100
1081/1081 [==============================] - 16s 15ms/step - loss: 22.6876 - val_loss: 19.8865
Epoch 7/100
1081/1081 [==============================] - 17s 16ms/step - loss: 22.2572 - val_loss: 19.4477
Epoch 8/100
1081/1081 [==============================] - 18s 16ms/step - loss: 22.0494 - val_loss: 20.0174
Epoch 9/100
1081/1081 [==============================] - 16s 15ms/step - los

Epoch 52/100
1081/1081 [==============================] - 11s 11ms/step - loss: 21.4544 - val_loss: 19.1933
Epoch 53/100
1081/1081 [==============================] - 11s 10ms/step - loss: 21.4716 - val_loss: 19.1751
Epoch 54/100
1081/1081 [==============================] - 10s 9ms/step - loss: 21.4476 - val_loss: 19.1584
Epoch 55/100
1081/1081 [==============================] - 11s 10ms/step - loss: 21.4721 - val_loss: 19.4608
Epoch 56/100
1081/1081 [==============================] - 10s 9ms/step - loss: 21.7126 - val_loss: 19.1585
Epoch 57/100
1081/1081 [==============================] - 11s 10ms/step - loss: 21.5437 - val_loss: 19.6362
Epoch 58/100
1081/1081 [==============================] - 11s 10ms/step - loss: 21.5129 - val_loss: 19.0856
Epoch 59/100
1081/1081 [==============================] - 12s 11ms/step - loss: 21.4609 - val_loss: 19.0619
Epoch 60/100
1081/1081 [==============================] - 10s 10ms/step - loss: 21.6687 - val_loss: 19.0506
Epoch 61/100
1081/1081 [======

540/540 [==============================] - 26s 47ms/step - loss: 24.4436 - val_loss: 20.9412
Epoch 28/100
540/540 [==============================] - 25s 46ms/step - loss: 23.8931 - val_loss: 20.6675
Epoch 29/100
540/540 [==============================] - 26s 48ms/step - loss: 23.4723 - val_loss: 20.4932
Epoch 30/100
540/540 [==============================] - 24s 44ms/step - loss: 23.1077 - val_loss: 20.2566
Epoch 31/100
540/540 [==============================] - 26s 49ms/step - loss: 22.8408 - val_loss: 20.4740
Epoch 32/100
540/540 [==============================] - 25s 47ms/step - loss: 22.6790 - val_loss: 20.1600
Epoch 33/100
540/540 [==============================] - 28s 51ms/step - loss: 22.5071 - val_loss: 19.9588
Epoch 34/100
540/540 [==============================] - 26s 47ms/step - loss: 22.4838 - val_loss: 20.1359
Epoch 35/100
540/540 [==============================] - 24s 44ms/step - loss: 22.2535 - val_loss: 20.3810
Epoch 36/100
540/540 [==============================] - 27s

540/540 [==============================] - 6s 11ms/step - loss: 21.6612 - val_loss: 19.5325
Epoch 83/100
540/540 [==============================] - 6s 11ms/step - loss: 21.5628 - val_loss: 19.5641
Epoch 84/100
540/540 [==============================] - 5s 10ms/step - loss: 21.6361 - val_loss: 19.5509
Epoch 85/100
540/540 [==============================] - 6s 12ms/step - loss: 21.5623 - val_loss: 19.5762
Epoch 86/100
540/540 [==============================] - 6s 12ms/step - loss: 21.5985 - val_loss: 19.7787
Epoch 87/100
540/540 [==============================] - 6s 12ms/step - loss: 21.6315 - val_loss: 19.8763
Epoch 88/100
540/540 [==============================] - 6s 11ms/step - loss: 21.5877 - val_loss: 19.6237
Epoch 89/100
540/540 [==============================] - 6s 11ms/step - loss: 21.5731 - val_loss: 19.5348
Epoch 90/100
540/540 [==============================] - 6s 10ms/step - loss: 21.6027 - val_loss: 19.7858
Epoch 91/100
540/540 [==============================] - 5s 10ms/step

...

528/528 [==============================] - 5s 10ms/step - loss: 20.9472 - val_loss: 22.7107
Epoch 48/100
528/528 [==============================] - 5s 10ms/step - loss: 20.9760 - val_loss: 22.6612
Epoch 49/100
528/528 [==============================] - 5s 10ms/step - loss: 20.9943 - val_loss: 22.5953
Epoch 50/100
528/528 [==============================] - 5s 10ms/step - loss: 20.9947 - val_loss: 22.5212
Epoch 51/100
528/528 [==============================] - 5s 10ms/step - loss: 20.9346 - val_loss: 22.8894
Epoch 52/100
528/528 [==============================] - 5s 10ms/step - loss: 20.9711 - val_loss: 22.4882
Epoch 53/100
528/528 [==============================] - 5s 10ms/step - loss: 20.9451 - val_loss: 22.6378
Epoch 54/100
528/528 [==============================] - 5s 10ms/step - loss: 20.9444 - val_loss: 22.5388
Epoch 55/100
528/528 [==============================] - 5s 10ms/step - loss: 20.9682 - val_loss: 22.5396
Epoch 56/100
528/528 [==============================] - 5s 10ms/step

528/528 [==============================] - 36s 67ms/step - loss: 21.2918 - val_loss: 22.7418
RNN learn complete
Epoch 1/100
528/528 [==============================] - 8s 13ms/step - loss: 168.4955 - val_loss: 142.6103
Epoch 2/100
528/528 [==============================] - 7s 13ms/step - loss: 127.4712 - val_loss: 105.2521
Epoch 3/100
528/528 [==============================] - 7s 13ms/step - loss: 96.0743 - val_loss: 76.2744
Epoch 4/100
528/528 [==============================] - 7s 13ms/step - loss: 72.0379 - val_loss: 54.8822
Epoch 5/100
528/528 [==============================] - 7s 12ms/step - loss: 54.5934 - val_loss: 41.2757
Epoch 6/100
528/528 [==============================] - 7s 13ms/step - loss: 41.9937 - val_loss: 32.0794
Epoch 7/100
528/528 [==============================] - 7s 13ms/step - loss: 33.3629 - val_loss: 27.6141
Epoch 8/100
528/528 [==============================] - 8s 15ms/step - loss: 28.3771 - val_loss: 25.3915
Epoch 9/100
528/528 [==============================]

528/528 [==============================] - 7s 13ms/step - loss: 20.8148 - val_loss: 22.4777
Epoch 79/100
528/528 [==============================] - 7s 13ms/step - loss: 20.8968 - val_loss: 22.5260
Epoch 80/100
528/528 [==============================] - 7s 13ms/step - loss: 20.8942 - val_loss: 22.5440
Epoch 81/100
528/528 [==============================] - 7s 13ms/step - loss: 20.9087 - val_loss: 22.6176
Epoch 82/100
528/528 [==============================] - 7s 13ms/step - loss: 20.8718 - val_loss: 22.6002
Epoch 83/100
528/528 [==============================] - 7s 13ms/step - loss: 20.8856 - val_loss: 22.6777
Epoch 84/100
528/528 [==============================] - 7s 12ms/step - loss: 20.8503 - val_loss: 22.4924
Epoch 85/100
528/528 [==============================] - 7s 13ms/step - loss: 20.8607 - val_loss: 22.7043
Epoch 86/100
528/528 [==============================] - 7s 13ms/step - loss: 20.8370 - val_loss: 22.3835
Epoch 87/100
528/528 [==============================] - 6s 12ms/step

528/528 [==============================] - 10s 18ms/step - loss: 21.0770 - val_loss: 22.5455
Epoch 33/100
528/528 [==============================] - 10s 19ms/step - loss: 21.1423 - val_loss: 22.5507
Epoch 34/100
528/528 [==============================] - 10s 19ms/step - loss: 21.0614 - val_loss: 22.6240
Epoch 35/100
528/528 [==============================] - 10s 18ms/step - loss: 21.1066 - val_loss: 22.6795
Epoch 36/100
528/528 [==============================] - 10s 18ms/step - loss: 21.0928 - val_loss: 22.5298
Epoch 37/100
528/528 [==============================] - 10s 20ms/step - loss: 21.0208 - val_loss: 22.5928
Epoch 38/100
528/528 [==============================] - 10s 19ms/step - loss: 21.0805 - val_loss: 22.5863
Epoch 39/100
528/528 [==============================] - 10s 19ms/step - loss: 21.0505 - val_loss: 22.5338
Epoch 40/100
528/528 [==============================] - 10s 19ms/step - loss: 21.0001 - val_loss: 22.6259
Epoch 41/100
528/528 [==============================] - 10s

528/528 [==============================] - 5s 10ms/step - loss: 21.3256 - val_loss: 22.6083
Epoch 88/100
528/528 [==============================] - 5s 10ms/step - loss: 21.1180 - val_loss: 22.7930
Epoch 89/100
528/528 [==============================] - 6s 11ms/step - loss: 21.0150 - val_loss: 22.5620
Epoch 90/100
528/528 [==============================] - 6s 11ms/step - loss: 20.9061 - val_loss: 22.5683
Epoch 91/100
528/528 [==============================] - 5s 10ms/step - loss: 20.8454 - val_loss: 22.4959
Epoch 92/100
528/528 [==============================] - 6s 11ms/step - loss: 20.9759 - val_loss: 22.6221
Epoch 93/100
528/528 [==============================] - 6s 11ms/step - loss: 20.9147 - val_loss: 22.4390
Epoch 94/100
528/528 [==============================] - 6s 11ms/step - loss: 20.8432 - val_loss: 22.5514
Epoch 95/100
528/528 [==============================] - 6s 11ms/step - loss: 20.8940 - val_loss: 22.5810
Epoch 96/100
528/528 [==============================] - 6s 11ms/step